<a href="https://colab.research.google.com/github/adityasingh1993/NLP-ANN/blob/master/Toxic_Comment.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
 !pip install kaggle

In [14]:
from google.colab import files
files.upload()

Saving kaggle.json to kaggle.json


{'kaggle.json': b'{"username":"adityasinghce92","key":"e79766a1206ef2fd74c1f97860d95521"}'}

In [0]:
!mkdir -p ~/.kaggle
!cp kaggle.json ~/.kaggle/

In [0]:
!chmod 600 ~/.kaggle/kaggle.json

In [17]:
!kaggle competitions download -c jigsaw-toxic-comment-classification-challenge

  0% 0.00/1.39M [00:00<?, ?B/s]
100% 1.39M/1.39M [00:00<00:00, 47.2MB/s]
 47% 11.0M/23.4M [00:00<00:00, 39.1MB/s]
100% 23.4M/23.4M [00:00<00:00, 67.2MB/s]
  0% 0.00/1.46M [00:00<?, ?B/s]
100% 1.46M/1.46M [00:00<00:00, 90.7MB/s]
 49% 13.0M/26.3M [00:00<00:00, 132MB/s]
100% 26.3M/26.3M [00:00<00:00, 129MB/s]


In [18]:
!pip install contractions
!pip install inflect

In [0]:
	
#!wget --header="Host: downloads.cs.stanford.edu" --header="User-Agent: Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/79.0.3945.117 Safari/537.36" --header="Accept: text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.9" --header="Accept-Language: en-IN,en;q=0.9,en-GB;q=0.8,en-US;q=0.7,hi;q=0.6" --header="Cookie: _ga=GA1.2.778886217.1559722518; _mkto_trk=id:194-OCQ-487&token:_mch-stanford.edu-1560092631271-53052; _gid=GA1.2.1948571120.1579118412" --header="Connection: keep-alive" "http://downloads.cs.stanford.edu/nlp/data/glove.6B.zip" -O "glove.6B.zip" -c


In [0]:
#!unzip glove.6B.zip 

In [0]:
import pandas as pd
import re, string, unicodedata
import nltk
import contractions
import inflect
from bs4 import BeautifulSoup
from nltk import word_tokenize, sent_tokenize
from nltk.corpus import stopwords

from nltk.stem import LancasterStemmer, WordNetLemmatizer
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.models import Model,Input
from keras.layers import LSTM, Embedding, Dense, TimeDistributed, Dropout, Bidirectional,CuDNNLSTM,Add
from keras.layers import Bidirectional, GlobalMaxPool1D

In [0]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load in 

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the "../input/" directory.
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# Any results you write to the current directory are saved as output.

In [22]:
!ls

kaggle.json  sample_submission.csv.zip	test_labels.csv.zip
sample_data  test.csv.zip		train.csv.zip


In [23]:
!unzip train.csv.zip
!unzip test.csv.zip
!unzip test_labels.csv.zip

!unzip sample_submission.csv.zip

Archive:  train.csv.zip
  inflating: train.csv               
Archive:  test.csv.zip
  inflating: test.csv                
Archive:  test_labels.csv.zip
  inflating: test_labels.csv         
Archive:  sample_submission.csv.zip
  inflating: sample_submission.csv   


In [0]:
dataframe_train=pd.read_csv("train.csv")
dataframe_test=pd.read_csv("test.csv")
dataframe_test_label=pd.read_csv("test_labels.csv")

In [0]:
dataframe_train=pd.read_csv("train.csv")
dataframe_test=pd.read_csv("test.csv")
dataframe_test_label=pd.read_csv("test_labels.csv")

In [0]:
import re
def replace_contractions(text):
    return contractions.fix(text)
def cleanText(text):
    text = text.strip().replace("\n", " ").replace("\r", " ")
    text = replace_contractions(text)
    #text = replace_links(text, "link")
    #text = remove_numbers(text)
    text = re.sub(r'[,!@#$%^&*)(|/><";:.?\'\\}{]',"",text)
    text = text.lower()
    return text

In [0]:
listsentence=list(dataframe_train["comment_text"])
listsentence_test=list(dataframe_test["comment_text"])

In [0]:
listcleansentence=[]
for i in listsentence:
    listcleansentence.append(cleanText(i))

In [0]:
listcleansentence_test=[]
for i in listsentence_test:
    
    try:
        listcleansentence_test.append(cleanText(i))
    except:
        listcleansentence_test.append(i)

In [0]:
allsentences=listcleansentence_test+listcleansentence

In [0]:
words=" ".join(allsentences).split(" ")

In [0]:
word2idx={w:i for i,w in enumerate(words)}

In [0]:
id2word={}
for key,val in word2idx.items():
    id2word[val]=key

In [0]:
maxvocab=max(list(word2idx.values()))

In [0]:
tokenizer = Tokenizer(num_words=maxvocab)
tokenizer.fit_on_texts(allsentences)
input_sequence = tokenizer.texts_to_sequences(listsentence)


In [0]:
inputx = pad_sequences(input_sequence, maxlen=3000, dtype='int32', padding='post', truncating='post')

In [0]:
def glove_100d_dictionary():
  embeddings_index = {}
  f = open('glove.6B.100d.txt')
  for line in f:
      values = line.split()
      word = values[0]
      coefs = np.asarray(values[1:], dtype='float32')
      embeddings_index[word] = coefs
  f.close()
  return embeddings_index

In [0]:
listofabsentword=[]
def embedding_matrix_creater(embedding_dimention):
  embeddings_index=glove_100d_dictionary()
  embedding_matrix = np.zeros((len(word2idx) + 1, embedding_dimention))
  for word, i in word2idx.items():
      embedding_vector = embeddings_index.get(word)
      if embedding_vector is not None:
          # words not found in embedding index will be all-zeros.
          try:
            embedding_matrix[i] = embedding_vector
          except:
            listofabsentword.append(word)
            print("exception===>",word)
            pass
  return embedding_matrix

In [0]:
def embedding_layer_creater(VOCAB_SIZE, EMBEDDING_DIM, MAX_LEN, embedding_matrix):
  
  embedding_layer = Embedding(input_dim = VOCAB_SIZE, 
                              output_dim = EMBEDDING_DIM,
                              input_length = MAX_LEN,
                              weights = [embedding_matrix],
                              trainable = False)
  return embedding_layer

In [0]:
embedding_matrix=embedding_matrix_creater(100)
embedding_layer = embedding_layer_creater(maxvocab, 100, 3000, embedding_matrix)

exception===> yo
exception===> bitch
exception===> ja
exception===> rule
exception===> is
exception===> more
exception===> succesful
exception===> then
exception===> you
exception===> will
exception===> ever
exception===> be
exception===> what
exception===> up
exception===> with
exception===> and
exception===> hating
exception===> sad
exception===> should
exception===> slap
exception===> ur
exception===> white
exception===> faces
exception===> get
exception===> to
exception===> kiss
exception===> my
exception===> ass
exception===> guys
exception===> sicken
exception===> me
exception===> about
exception===> pride
exception===> in
exception===> da
exception===> music
exception===> man
exception===> do
exception===> not
exception===> diss
exception===> that
exception===> shit
exception===> on
exception===> him
exception===> nothin
exception===> wrong
exception===> bein
exception===> like
exception===> tupac
exception===> he
exception===> was
exception===> a
exception===> brother
exception

In [0]:
y=dataframe_train.iloc[:,2:].values

In [41]:
inputs = Input(shape=(3000,))
#emb_layer = Embedding(input_dim = 506004, output_dim = 100,input_length = 3000,weights = [embedding_matrix],trainable = False)(inp)
#emb_layer = Embedding(1000, 100, weights=embedding_matrix)(inp)
emb_layer = Embedding(input_dim = 506004, output_dim = 100,input_length = 3000)(inputs)
print(emb_layer)




Tensor("embedding_1/embedding_lookup/Identity:0", shape=(?, 3000, 100), dtype=float32)


In [43]:
lstm_layer1 = Bidirectional(CuDNNLSTM(100, return_sequences=True))(emb_layer)
print(lstm_layer1)
#dropout_layer = Dropout(0.5)(lstm_layer1)
lstm_layer2 = Bidirectional(CuDNNLSTM(100, return_sequences=True))(lstm_layer1)
concat_layer= Add()([lstm_layer1,lstm_layer2])
maxpool_layer = GlobalMaxPool1D()(concat_layer)
dense_layer = Dense(50, activation="relu")(maxpool_layer)
dropout_layer = Dropout(0.5)(dense_layer)
dense_layer2 = Dense(6, activation="sigmoid")(dropout_layer)
model = Model(inputs=inputs, outputs=dense_layer2)
model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

Tensor("bidirectional_2/concat_2:0", shape=(?, 3000, 200), dtype=float32)

Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


In [0]:
model.summary()

Model: "model_1"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_1 (InputLayer)            (None, 3000)         0                                            
__________________________________________________________________________________________________
embedding_1 (Embedding)         (None, 3000, 100)    50600400    input_1[0][0]                    
__________________________________________________________________________________________________
bidirectional_15 (Bidirectional (None, 3000, 200)    161600      embedding_1[0][0]                
__________________________________________________________________________________________________
bidirectional_16 (Bidirectional (None, 3000, 200)    241600      bidirectional_15[0][0]           
____________________________________________________________________________________________

In [0]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test=train_test_split(inputx,y)

In [0]:
model.fit(X_train,y_train,batch_size=32,verbose=1,validation_split=0.1,epochs=15,workers=3, use_multiprocessing=True)

Train on 107710 samples, validate on 11968 samples
Epoch 1/15
 50464/107710 [=============>................] - ETA: 17:41 - loss: 0.0974 - acc: 0.9698

In [0]:
from sklearn.metrics import roc_curve,roc_auc_score
ypredtest=model.predict(X_test)



NameError: ignored

In [0]:
y_test

array([[0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [1, 0, 1, 0, 1, 0],
       ...,
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0],
       [0, 0, 0, 0, 0, 0]])

In [0]:
from google.colab import drive
drive.mount('/content/drive')

In [0]:
 roc_auc_score ( y_test , ypredtest,average="macro")

0.9611426537141122

In [0]:
import matplotlib.pyplot as plt
def plot_roc_curve(fpr,tpr): 
  plt.plot(fpr,tpr) 
  plt.axis([0,1,0,1]) 
  plt.xlabel('False Positive Rate') 
  plt.ylabel('True Positive Rate') 
  plt.show()  

In [0]:
input_sequence_test=tokenizer.texts_to_sequences(listsentence_test)
inputx_test=pad_sequences(input_sequence_test, maxlen=3000, dtype='int32', padding='post', truncating='post')
listres=[]

In [0]:
ypred=model.predict(inputx_test)

In [0]:
sampledf=pd.read_csv("sample_submission.csv")

In [0]:
classlist=['toxic', 'severe_toxic', 'obscene', 'threat', 'insult',
       'identity_hate']

In [0]:
sampledf[classlist]=ypred

In [0]:
sampledf.to_csv("submission5.csv", index=False)

In [0]:
!ls

kaggle.json		   submission4.csv  test_labels.csv
sample_data		   submission5.csv  test_labels.csv.zip
sample_submission.csv	   test.csv	    train.csv
sample_submission.csv.zip  test.csv.zip     train.csv.zip


In [0]:
from google.colab import files
files.download("submission5.csv") 

MessageError: ignored